# HexMagic

> Fill in a module description here

```python
#| default_exp core
```

In [ ]:
#| default_exp core

In [ ]:
#| hide
from nbdev.showdoc import *
from nbdev import nbdev_export

In [ ]:
nbdev_export()

In [ ]:
#| export
#| hide
#import nbdev; nbdev.nbdev_export()
import sys
import math
from fastcore.basics import patch

#| export
## Introduction

The purpose of this library is to generate hex maps that are used in board games.

#| export
## Getting Started

In [ ]:
#| export
from HexMagic.plot.primitives import  MapCord , PrimitiveDemo
from HexMagic.plot.hex import Hex


from HexMagic.styles import StyleCSS,  SVGBuilder

In [ ]:
#| export
from HexMagic.primitives import MapPath, MapSize, MapRect, MapCord 
from HexMagic.primitives import HexGrid, HexPosition ,  HexRegion, GosperCurve, windy_edge , unique_windy_edge

import numpy as np

from HexMagic.terrain import Terrain
from HexMagic.voronoi import generate_plate_terrain


Terrain.fromSeeds = generate_plate_terrain
from HexMagic.climate import ClimatePreset, Climate, TerraDemo
from HexMagic.geology import Geology, DrainageBasins


In [ ]:
def demoTerr():

    mySize = MapSize(480,480)
    myBounds = MapRect(MapCord(0,0), mySize)
    
    sampleMap, plates =  Terrain.fromSeeds(myBounds,radius=15)

    sampleMap.colorMap()
    sgrid = sampleMap.hexGrid
    sgrid.builder.adjust("regions", sgrid.styleLayer(f=windy_edge(iterations=2, offset_factor=0.1)))
    #sampleMap.hexGrid.update()

    return sampleMap.hexGrid.builder.show()

In [ ]:
demoTerr()

In [ ]:
from HexMagic.terrainpatterns import TerrainPatterns
from HexMagic.climate import TerrainFactory

## Climate

In [ ]:

baMap = TerraDemo().bayArea_map()
baWorld = Geology(baMap,[],"San Francisco Bay Area")

#baMap = TerraDemo().california_map()
#baWorld = Geology(baMap,[],"California")

baWorld.baseMap(showHexes=False)



In [ ]:
??Geology.baseMap


```python
@patch
def baseMap(self:Geology,showHexes=True):


    grid = self.terrain.hexGrid
    builder = grid.builder
    builder.layers = []
    self.terrain.colorMap()
    if showHexes:
        grid.update()
    else:
        builder.adjust("elevations", grid.styleLayerOrdered(
        styles=self.terrain.colorLevels,
        f=unique_windy_edge(iterations=3)))

    builder.adjust("watersheds", self.basins.draw_watersheds())
    #builder.adjust("legend",builder.legendOverlay(self.terrain.colorLevels,width=100))
    builder.adjust("legend", builder.legendBelow(self.terrain.colorLevels, use_hex=True))
    legend_text = f"{self.name}"

    self.terrain.hexGrid.builder.add_centered_text(
        legend_text, 
        y_offset=-self.terrain.hexGrid.builder.height/2 + 30,
        class_name="watershed_legend"
    )

    return builder.show()
```

**File:** `~/HexMagic/HexMagic/geology.py`

In [ ]:
baMap.builder.layers = []
mountains = baMap.find_peaks(7,0,exclusion_radius=9)
for i , epicenter in enumerate(mountains):
    baMap.elevations += baMap.volcano(center=epicenter, adjusted=50+ ((i+1)*30), num_rings=6)
baMap.colorMap()
baMap.hexGrid.update()
baMap.builder.show()

## Hydrology

In [ ]:
baMap = TerraDemo().hong_kong_map().downsample_climate(0.6)

baWorld = Geology(baMap,[],"Hong Kong")
baWorld.watershedMap()

In [ ]:
baWorld.climateDotMap()

In [ ]:
baMap = TerraDemo().bayArea_map()
baWorld = Geology(baMap,[],"San Francisco Bay Area")
baWorld.climateIconMap(scale=5)

In [ ]:
baMap = TerraDemo().california_map().downsample_climate(0.6)
baWorld = Geology(baMap,[],"California Dreaming")
baWorld.weatherMap()

In [ ]:
def showclimates(terrain,saturation=0.8):

    basin = DrainageBasins(terrain)

     
    terrain.hexGrid.builder.adjust("watersheds", basin.dotted_watershed_overlay(min_density=0.5))
    terrain.hexGrid.builder.adjust("borders",terrain.elevation_borders())

       # Add gradient flow lines
    gradient_overlay = basin.gradient_overlay(
        min_width=0.5,
        max_width=4.0,
        opacity=0.7
    )

    river_style = StyleCSS(
        "nile",
        fill = "none",
        stroke= '#23194629',
        stroke_width=3,
        opacity= 0.7
    )
    
    terrain.hexGrid.builder.add_style(river_style)
    river_svg = ""

    mainBasins = basin.get_major(6)
    
    for basin in mainBasins:
        small_river = basin.simplify(2)
        small_river.tributary.terrain = terrain
        river_svg += small_river.draw()

    sgrid = terrain.hexGrid
    sgrid.builder.layers = []




    climate_colors = {
        Climate.MARINE.value: "#1e88e5",
        Climate.FRESHWATER.value: "#42a5f5",
        Climate.TUNDRA.value: "#e3f2fd",
        Climate.DESERT.value: "#fdd835",
        Climate.GRASSLAND.value: "#9ccc65",
        Climate.FOREST.value: "#2e7d32",
        Climate.JUNGLE.value: "#1b5e20",
    }
    
    if 'climate' not in terrain.fields:
        terrain.compute_climate()
    
    climate_indices = terrain.fields['climate'].astype(int)
    styles = [StyleCSS(f"climate_{i}",fill = climate_colors[i]) for i in range(len(Climate))]
    #styles = [ for x in styles]
    for style in styles:
        style.properties["fill"] = style.desaturate(saturation)
        terrain.hexGrid.builder.add_style(style)

    
    #work
    sgrid = terrain.hexGrid
    print(climate_indices[:20])
    climateRegions = sgrid.regions_by_value(climate_indices)
    retLayer = ""
    
    borders = {}  # Shared cache across all regions
    
    overlay = ""
    for region in climateRegions:
    
        idx  =  region.hexes.pop()
        region.hexes.add(idx)
        
        styleI = int(climate_indices[idx])
        style = styles[styleI]
        print(idx,styleI,len(region.hexes))

        for path in region.trace_perimeter_cached(borders,
          style=style,
          f=unique_windy_edge(iterations=2)):
                overlay += path.svg()

    return overlay + river_svg
 


In [ ]:


overlay = showclimates(baMap,0.25)
baMap.hexGrid.builder.layers = []
baMap.hexGrid.builder.adjust("climate",overlay)
baMap.hexGrid.builder.show()



[5 5 5 5 4 4 0 0 4 4 0 0 0 0 0 0 0 0 0 0]
6 0 984


1540 3 226
1024 4 173
0 5 367


In [ ]:

from HexMagic.terraform import Terraform
from HexMagic.styles import apply_looping_animation, LoopingLayerAnimation


In [ ]:

@patch
def longRun(self:TerraDemo,num_snapshots=3,debug = False):
    baMap = TerraDemo().bayArea_map()
    baMap.compute_climate()
    siliconValley = Terraform(baMap)

  
    org = baMap.clone()
    
    # Store snapshots
    snapshots = []

    for i in range(num_snapshots):
        print(f"on interval {i}")
         
        basins = DrainageBasins(baMap, debug=debug)
        major_watersheds = basins.get_major(top_n=25)
        
        for watershed in major_watersheds:
            if watershed.is_ocean:  # Only ocean-draining watersheds get deltas
               baMap.buildUp(watershed,rings=2,ele=7)

        mountains = baMap.find_peaks(7,0,exclusion_radius=9)
        for i , epicenter in enumerate(mountains):
            baMap.elevations += baMap.volcano(center=epicenter, adjusted=70+ ((i+1)*30), num_rings=6)

        rivers = baMap.carve_to_ocean(num_lakes=1)
        baMap.compute_climate()
        baMap.colorMap()
        #overlay = siliconValley.terrain.hexGrid.styledHexes()
        overlay = baMap.hexGrid.styleLayer(f=windy_edge(iterations=2, offset_factor=0.1))
        overlay += basins.draw_watersheds()

        overlay  += f'<text x="{40}" y="{15}" text-anchor="middle" stroke="white">{i}</text>'
        #overlay = showclimates(baMap,0.25)
        
        snapshots.append(overlay)

        
    retTerrain = siliconValley.terrain.clone()
    retTerrain.builder.layers = []
    names = []
    for i , overlay in enumerate(snapshots):
        name = f"time_{i}"
        retTerrain.builder.adjust(f"time_{i}",overlay)
        names.append(name)

    anim = LoopingLayerAnimation(names, visible_count=2, step_duration=2, fade_duration=0.1, dim_opacity=0)
    apply_looping_animation( retTerrain.hexGrid.builder,anim)

    climate_colors = {
        Climate.MARINE.value: "#1e88e5",
        Climate.FRESHWATER.value: "#42a5f5",
        Climate.TUNDRA.value: "#e3f2fd",
        Climate.DESERT.value: "#fdd835",
        Climate.GRASSLAND.value: "#9ccc65",
        Climate.FOREST.value: "#2e7d32",
        Climate.JUNGLE.value: "#1b5e20",
    }
    

    
    saturation = 0.2
    styles = [StyleCSS(f"climate_{i}",fill = climate_colors[i]) for i in range(len(Climate))]
    #styles = [ for x in styles]
    for style in styles:
        style.properties["fill"] = style.desaturate(saturation)
        retTerrain.hexGrid.builder.add_style(style)

    return retTerrain



In [ ]:
allThings = TerraDemo().longRun(num_snapshots=8,debug=False)
allThings.hexGrid.builder.show()

on interval 0


Done at iter 1: 1 lakes
on interval 1


Done at iter 1: 1 lakes


on interval 2


Done at iter 1: 1 lakes


...

Done at iter 1: 1 lakes


on interval 6


Done at iter 1: 1 lakes


on interval 7


Done at iter 1: 1 lakes
